In [1]:
import sys
sys.path.append('../')
import joblib

from scipy.signal import savgol_filter

from Modules.Utils.Imports import *
from Modules.Utils.DRUMSLasso import *
from Modules.Utils.GetLowestGPU import *
import Modules.Loaders.DataFormatter as DF
from Modules.Models.BuildBINNs import AdaMaskBINNCovasim
from Modules.Models.BuildBINNs import chi
from Modules.Utils.ModelWrapper import ModelWrapper

from Notebooks.utils import get_case_name
from queue import PriorityQueue

c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
device = torch.device(GetLowestGPU(pick_from=[0,1,2,3]))
# helper functions
def to_torch(x):
    return torch.from_numpy(x).float().to(device)
def to_numpy(x):
    return x.detach().cpu().numpy()

Device set to cpu


In [3]:
# instantiate BINN model parameters and path
path = '../Data/covasim_data/drums_data/'

population = int(500e3)
test_prob = 0.1
trace_prob = 0.3
keep_d = True
retrain = False
dynamic = True
masking = 3
multiple = True
parallelb = True
n_runs = 64
chi_type = 'piecewise'

# model parameters
maskb = True
masking_learned = False

case_name = get_case_name(population, test_prob, trace_prob, keep_d, dynamic=dynamic, chi_type=chi_type)

In [4]:
if not masking==0:
    if masking==1:
        case_name = case_name + '_maskingdem'
    elif masking==2:
        case_name = case_name + '_maskinguni'
    elif masking==3:
        case_name = case_name + '_maskingnorm'

if multiple:
    params = DF.load_covasim_data(path, population, test_prob, trace_prob, keep_d, case_name + '_' + str(n_runs), plot=False)
else:
    params = DF.load_covasim_data(path, population, test_prob, trace_prob, keep_d, case_name, plot=False)

In [5]:
# multiple==True and parallelb==False means that data is a list and not normalized
if multiple and not parallelb:
    data = np.mean(params['data'], axis=0)
    data = (data / params['population'])
    avg_masking = np.mean(params['avg_masking'], axis=0)
    avg_masking = (avg_masking / params['population'])
# multiple==True and parallelb==True means that the data is a 2d array and normalized
elif multiple and parallelb:
    data = params['data'] # parallel simulations store normalized data
    avg_masking = params['avg_masking']
# otherwise, the data is from a single simulation and is not normalized
else:
    data = params['data']
    data = (data / params['population']).to_numpy()
    avg_masking = params['avg_masking']
    avg_masking = (avg_masking / params['population'])
    
params.pop('data')

N = len(data)
t_max = N - 1
t = np.arange(N)[:,None]

tracing_array = params['tracing_array']

In [6]:
model_path = '../models/covasim'
if maskb:
    model_path += '/mask'
    if masking_learned:
        model_path += '/learned_masking'
    else:
        model_path += '/observed_masking'
else:
    model_path += '/no_mask'

In [7]:
#--------------------no masking----------------------#
# model_folder = '/2023-07-20_17-53-03' # no masking, 500e3 pop, dynamic piecewise, 64 avg., 800e3 epochs, lr=1e-5
# model_folder = '/2023-07-21_18-42-24' # no masking, 500e3 pop, dynamic piecewise, 64 avg., 1e6 epochs, lr=1e-6
# model_folder = '/2023-07-22_10-20-01' # no masking, 500e3 pop, dynamic piecewise, 64 avg., 1e6 epochs, lr=5e-6
# model_folder = '/2023-07-23_00-48-24' # no masking, 500e3 pop, dynamic piecewise, 64 avg., 1e6 epochs, lr=9e-6
# model_folder = '/2023-07-23_15-17-23' # no masking, 500e3 pop, dynamic piecewise, 64 avg., 1e6 epochs, lr=9e-6
# model_folder = '/2023-07-24_23-10-16' # no masking, 500e3 pop, dynamic piecewise, 64 avg., 1e6 epochs, lr=1e-5

#------------------normal masking--------------------#
# model_folder = '/2023-07-20_18-13-01' # masking-norm, observed M, 500e3, dynamic piecewise, 64 avg., 800e3, lr=5e-5
# model_folder = '/2023-07-21_18-41-30' # masking-norm, observed M, 500e3, dynamic piecewise, 64 avg., 800e3, lr=5e-5
# model_folder = '/2023-07-21_21-48-16' # masking-norm, observed M, 1e6, dynamic piecewise, 64 avg., 800e3, lr=5e-5
model_folder = '/2023-07-22_10-16-47' # masking-norm, observed M, 1e6, dynamic piecewise, 64 avg., 800e3, lr=5e-5
# model_folder = '/2023-07-22_12-30-47' # masking-norm, observed M, 1e6, dynamic piecewise, 64 avg., 800e3, lr=5e-5
# model_folder = '/2023-07-23_00-01-28' # masking-norm, observed M, 1e6, dynamic piecewise, 64 avg., 800e3, lr=5e-5
# model_folder = '/2023-07-23_00-27-07' # masking-norm, observed M, 1e6, dynamic piecewise, 64 avg., 800e3, lr=5e-5
# model_folder = '/2023-07-23_15-14-54' # masking-norm, observed M, 1e6, dynamic piecewise, 64 avg., 800e3, lr=4e-5

#---------------demographic masking------------------#
# model_folder = '/2023-07-20_22-20-10' # masking-dem, observed M, 500e3, dynamic piecewise, 64 avg., 600e3, lr=5e-5
# model_folder = '/2023-07-23_15-15-56' # masking-dem, observed M, 500e3, dynamic piecewise, 64 avg., 600e3, lr=3e-6
# model_folder = '/2023-07-24_23-09-21' # masking-dem, observed M, 500e3, dynamic piecewise, 64 avg., 600e3, lr=3e-6
# model_folder = '/2023-07-24_23-09-34' # masking-dem, observed M, 500e3, dynamic piecewise, 64 avg., 600e3, lr=3e-6


mydir = model_path + model_folder

In [8]:
# mydir = '../models/covasim/mask/2023-07-16_16-48-08' # norm masking, 500e3 pop, dynamic piecewise, keepd, 2048 avg., 800,000 epochs, lr=5e-5, deep eta, beta, tau_bounds = [0.08, 0.12]
# mydir = '../models/covasim/no_mask/2023-07-18_18-53-36' # no masking, 500e3 pop, dynamic piecewise, keepd, 64 avg., 500,000 epochs, lr=5e-5, deep eta, beta, tau_bounds = [0.05, 0.15]

In [9]:
yita_lb = 0.0
yita_ub = 1.0
beta_lb = 0.0
beta_ub = 0.5
tau_lb = 0.1
tau_ub = 0.3
eta_deep = True
beta_deep = True
tau_deep = False

In [10]:
binn = AdaMaskBINNCovasim(params, 
                t_max_real=t_max, 
                tracing_array=tracing_array, 
                yita_lb=None, 
                yita_ub=None,
                beta_lb=None,
                beta_ub=None,
                tau_lb=tau_lb,
                tau_ub=tau_ub, 
                chi_type=chi_type,
                eta_deep=eta_deep,
                beta_deep=beta_deep,
                tau_deep=tau_deep,
                maskb=maskb,
                masking_learned=masking_learned).to(device)
parameters = binn.parameters()
model = ModelWrapper(binn, None, None, save_name=os.path.join(mydir, case_name))

In [11]:
# load model weights
# model.save_name = '../Weights/'
# model.save_name += case_name
if retrain:
    model.save_name += '_retrain'
model.save_name += '_best_val'
model.load(model.save_name + '_model', device=device)
save_path = model.save_folder
# grab initial condition
u0 = data[0, :].copy()

In [12]:
# grab value ranges
yita_lb, yita_ub = model.model.yita_lb, model.model.yita_ub
beta_lb, beta_ub = model.model.beta_lb, model.model.beta_ub
tau_lb, tau_ub = model.model.tau_lb, model.model.tau_ub

In [13]:
# learned contact_rate function
def contact_rate(u):
    res = binn.eta_func(to_torch(u)) # [:,[0,3,4]]
    return to_numpy(res)

# learned effective tracing rate function
def beta(u):
    res = binn.beta_func(to_torch(u))
    return to_numpy(res)

# learned diagnosis of quarantined rate function
def tau(u):
    res = binn.tau_func(to_torch(u))
    return to_numpy(res)

def chi_func(t):
    chi_t = chi(1 + to_torch(t) * t_max, trace_prob, chi_type)
    return chi_t

In [14]:
if masking > 0:
    all_data = np.concatenate([data, avg_masking[:,None]], axis=1) # STEAYDQRFM
else:
    all_data = data

if maskb:
    eta_input = np.concatenate([data[:,[0,3,4]], avg_masking[:,None]], axis=1) #SAYM
else:
    eta_input = np.concatenate([data[:,[0,3,4]]], axis=1) #SAY
eta0 = contact_rate(eta_input) # eta(S,A,Y,M)
eta_values = yita_lb + (yita_ub - yita_lb) * eta0[:, 0][:, None]

chi_t = to_numpy(chi_func(t))
beta_input = np.concatenate([np.sum(data[:,[0,3,4]], axis=1)[:,None], chi_t], axis=1)
beta_values = beta(beta_input)

tau_input = data[:,[3,4]]
tau0 = tau(tau_input)
tau_values = tau_lb + (tau_ub - tau_lb) * tau0

In [15]:
def get_best_num_comps(num_comps=-1, pq=None):
    if pq.empty():
        raise Exception('The Priority Queue given is empty')
    bl_dict = pq.get()[-1]
    if num_comps==-1:
        return bl_dict
    if 'f ' in bl_dict['Equation'].split('+'):
        return bl_dict
    if len(bl_dict['Equation'].split('+')) - 1 <= num_comps:
        return bl_dict
    
    good_eq = False
    while not good_eq and not pq.empty():
        cand = pq.get()[-1]
        curr_num = len(cand['Equation'].split('+')) - 1
        if curr_num <= num_comps:
            good_eq = True
            return cand
    if not good_eq:
        raise Exception('No equation with that number of components was found')

***
### LASSO on $\eta$

In [17]:
all_comps = True

if all_comps:
    if maskb:
        comps = list('STEAYDQRFM')
    else:
        comps = list('STEAYDQRF')
    X_dict = {key : value for key, value in zip(comps, all_data.T)}
else:
    eta_input_data = all_data[:,[0,3,4,9]]
    if maskb:
        comps = list('SAYM')
    else:
        comps = list('SAY')
    X_dict = {key : value for key, value in zip(comps, eta_input_data.T)}

alphas_list = np.linspace(float(1e-8), float(1e-4), num=20000)

In [18]:
eq_set = set()
eq_q = PriorityQueue()
min_comps = 1000

for i in alphas_list:
    lasso_dict = DRUMS_Lasso(X_dict, eta_values, intercept=True,alphas=np.array([i]))
    if not lasso_dict['Equation'] in eq_set:
        eq_set.add(lasso_dict['Equation'])
        eq_q.put((lasso_dict['MSE'], i, lasso_dict['Equation'], lasso_dict))
        min_comps = len(lasso_dict['Equation'].split('+')) - 1
        if 'f ' in lasso_dict['Equation'].split('+'):
            break

c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:1561: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:620: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.00015287578437343224, tolerance: 3.452518202029044e-05
  model = cd_fast.enet_coordinate_descent_gram(
c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:620: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.0009364455747815775, tolerance: 0.00016657794006660355
  model = cd_fast.enet_coordinate_descent_gram(
c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\s

KeyboardInterrupt: 

In [ ]:
bl_dict = get_best_num_comps(pq=eq_q)
max_comps = len(bl_dict['Equation'].split('+')) - 1
best_list = [bl_dict]
for i in reversed(range(min_comps, max_comps)):
    nb_dict = get_best_num_comps(num_comps=i, pq=eq_q)
    best_list.append(nb_dict)

In [ ]:
if not os.path.exists(model.save_folder + '/eta_eq_coef'):
    os.makedirs(os.path.join(model.save_folder, 'eta_eq_coef'))
    
file_path = model.save_folder  + '/eta_eq_coef'

for i, elem in enumerate(reversed(best_list)):
    nb_file_name = case_name + '_' + str(n_runs) + '_sparse_coef_' + str(i + min_comps) + 'comps'
    joblib.dump(elem, os.path.join(file_path, nb_file_name), compress=True)

***
### LASSO on $\beta$

In [ ]:
if all_comps:
    comps = list('STEAYDQRF')
    X_dict = {key : value for key, value in zip(comps, all_data.T)}
else:
    beta_input_data = np.concatenate([np.sum(all_data[:,[0,3,4]], axis=1)[:,None], chi_t], axis=1)
    comps = list('sx')
    X_dict = {key : value for key, value in zip(comps, beta_input_data.T)}

alphas_list = np.linspace(float(1e-8), float(1e-4), num=20000)

NameError: name 'all_comps' is not defined

In [ ]:
eq_set = set()
eq_q = PriorityQueue()
min_comps = 1000

for i in alphas_list:
    lasso_dict = DRUMS_Lasso(X_dict, beta_values, intercept=True, alphas=np.array([i]))
    if not lasso_dict['Equation'] in eq_set:
        eq_set.add(lasso_dict['Equation'])
        eq_q.put((lasso_dict['MSE'], i, lasso_dict['Equation'], lasso_dict))
        min_comps = len(lasso_dict['Equation'].split('+')) - 1
        if 'f ' in lasso_dict['Equation'].split('+'):
            break

c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:1561: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:620: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 4.618892582605727e-05, tolerance: 2.115787776320408e-05
  model = cd_fast.enet_coordinate_descent_gram(
c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:620: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 3.855124016793887e-05, tolerance: 2.1074309635343453e-05
  model = cd_fast.enet_coordinate_descent_gram(
c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\sk

In [ ]:
bl_dict = get_best_num_comps(pq=eq_q)
max_comps = len(bl_dict['Equation'].split('+')) - 1
best_list = [bl_dict]
for i in reversed(range(min_comps, max_comps)):
    nb_dict = get_best_num_comps(num_comps=i, pq=eq_q)
    best_list.append(nb_dict)

In [ ]:
if not os.path.exists(model.save_folder + '/beta_eq_coef'):
    os.makedirs(os.path.join(model.save_folder, 'beta_eq_coef'))
    
file_path = model.save_folder  + '/beta_eq_coef'

for i, elem in enumerate(reversed(best_list)):
    nb_file_name = case_name + '_' + str(n_runs) + '_sparse_coef_' + str(i + min_comps) + 'comps'
    joblib.dump(elem, os.path.join(file_path, nb_file_name), compress=True)

***
### LASSO on $\tau$

In [ ]:
if all_comps:
    comps = list('STEAYDQRF')
    X_dict = {key : value for key, value in zip(comps, all_data.T)}
else:
    tau_input_data = all_data[:,[3,4]]
    comps = list('AY')
    X_dict = {key : value for key, value in zip(comps, tau_input_data.T)}
alphas_list = np.linspace(float(1e-8), float(1e-4), num=20000)

In [37]:
eq_set = set()
eq_q = PriorityQueue()
min_comps = 1000

for i in alphas_list:
    lasso_dict = DRUMS_Lasso(X_dict, tau_values, intercept=True, alphas=np.array([i]))
    if not lasso_dict['Equation'] in eq_set:
        eq_set.add(lasso_dict['Equation'])
        eq_q.put((lasso_dict['MSE'], i, lasso_dict['Equation'], lasso_dict))
        min_comps = len(lasso_dict['Equation'].split('+')) - 1
        if 'f ' in lasso_dict['Equation'].split('+'):
                break

c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:1561: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


In [38]:
bl_dict = get_best_num_comps(pq=eq_q)
max_comps = len(bl_dict['Equation'].split('+')) - 1
best_list = [bl_dict]
for i in reversed(range(min_comps, max_comps)):
    nb_dict = get_best_num_comps(num_comps=i, pq=eq_q)
    best_list.append(nb_dict)

In [39]:
if not os.path.exists(model.save_folder + '/tau_eq_coef'):
    os.makedirs(os.path.join(model.save_folder, 'tau_eq_coef'))
    
file_path = model.save_folder  + '/tau_eq_coef'

for i, elem in enumerate(reversed(best_list)):
    nb_file_name = case_name + '_' + str(n_runs) + '_sparse_coef_' + str(i + min_comps) + 'comps'
    joblib.dump(elem, os.path.join(file_path, nb_file_name), compress=True)

***
### Loading learned coefficients

In [40]:
print(f'The maximum number of components for tau: {max_comps}')

The maximum number of components for tau: 1


In [71]:
eta_dl = joblib.load(mydir + '/' + case_name + '/eta_eq_coef/' + case_name + '_' + str(n_runs) + '_sparse_coef_6comps')
beta_dl = joblib.load(mydir + '/' + case_name + '/beta_eq_coef/' + case_name + '_' + str(n_runs) + '_sparse_coef_3comps')
tau_dl = joblib.load(mydir + '/' + case_name + '/tau_eq_coef/' + case_name + '_' + str(n_runs) + '_sparse_coef_1comps')

In [72]:
eta_eq = eta_dl['Equation']
beta_eq = beta_dl['Equation']
tau_eq = tau_dl['Equation']

print(f'eta = {eta_eq[4:]}')
print(np.round(eta_dl['MSE'], 10))
print(f'beta = {beta_eq[4:]}')
print(np.round(beta_dl['MSE'], 10))
print(f'tau = {tau_eq[4:]}')
print(np.round(tau_dl['MSE'], 10))

eta = 2.90774*S + 3.46645*T + 0.67688*S^2 + 2.59345*S T + -1.31124*S M + 20.05466*M^2 + -3.24426
0.0001380123
beta = -0.90211*s + -0.26131*x + -0.22615*s^2 + 1.35927
1.6345e-06
tau = 0.10000
0.0
